# Jackson Botgess 2.0
### Trying to make something he hates even more

The goal: Make a new iteration of Jackson Botgess that instead of making mad-lib style quintains, will produce poems in Jackson's favorite style: Sonnets in Iambic Pentameter

### General Outline:
- Prepare text
    - Clean original poems
    - Remove Punctuation
    - Reverse
- Markov Models of Different State Sizes
    - for fun, word counts
- Rhyme Seeds
    - sonnet examples
    - list
    - function to make new list with input?
- Stress
    - testing for prexisting iambic pentameter
- Where the magic happens
    - rhyme seeds --> reversed lines
    - nested loops for couplets
        - going through markov models in decreasing state size
        - only selecting words with proper stress
    
    

## Preparing Text

I started by going through and removing all the titles of his poems and storing them in a separate txt file. 260 poems!!!! Jesus.

Then in the below cell I removed punctuation, capitalization, line breaks, and reversed the word order (so that the markov model would work backwards for rhyming).

In [1]:
jacksonCorpus = open("JBotCorpus.txt").read().strip("\n.,;:?!").split()
reverseCorpus = []
for i in range(len(jacksonCorpus)):
    reverseCorpus.append(jacksonCorpus[-1:][0])
    jacksonCorpus.pop(-1)
reverseJackson = " ".join(reverseCorpus)
reverseJackson = reverseJackson.replace(",","").replace(".","").replace("—"," ").replace("?","")
reverseJackson = reverseJackson.lower()
#back to list
reverseJackson = reverseJackson.split()
print(reverseJackson)

['ones', 'new', 'built', 'and', 'knees', 'and', 'hands', 'our', 'on', 'got', 'we', 'so', 'castles', 'the', 'all', 'destroyed', 'already', 'had', 'someone', 'smash', 'to', 'nothing', 'was', 'there', 'boardwalk', 'the', 'and', 'shop', 'taffy', 'the', 'past', 'out', 'beach', 'the', 'to', 'got', 'finally', 'i', 'and', 'brother', 'my', 'when', 'smash', 'to', 'something', 'for', 'looking', 'flashlights', 'and', 'shovels', 'with', 'eleven', 'at', 'out', 'went', 'i', 'and', 'brother', 'my', 'night', 'last', 'because', 'ruined', "they're", 'beach', 'the', 'down', 'and', 'up', 'castles', 'sand', 'ruined', 'of', 'dozens', 'and', 'hotel', 'rehoboth', 'my', 'outside', 'lines', 'power', 'the', 'in', 'tangled', 'kite', 'a', "there's", 'mouth', 'my', 'in', 'blood', 'there', 'is', 'mouth', 'why', 'my', 'in', 'blood', 'some', "there's", 'throats', 'our', 'in', 'caught', 'longer', 'no', 'are', 'pills', 'the', 'until', 'laugh', 'we’ll', 'and', 'friend', 'a', 'from', 'stolen', 'i’ve', 'car', 'a', 'in', 'ad

## Importing Modules

I need:
* random for random word selections
* pronouncing for rhyming and stresses
* collections for word count and dictionary

In [2]:
import random
import pronouncing as pr
from collections import Counter, defaultdict

## Word Counts 

Just for fun, lets see what Jackson's most commonly used words are.

### Most common non-basic words: 
* Love
* Night
* Man 
* Hands

eyyy ;)

### heart
* her (198)
* she (147), she's (32)
* woman (32)
* girl (32)
* lily (24)

### body parts
* back (129)
* eyes (85)
* hands (83), hand (40)
* hair (54)
* teeth (45)
* fingers (41)
* tongue (41)
* body (31)
* skin (25)
* lips (23)

### consumables
* coffee (44)
* smoke (43)
* blood (42)
* bar (37)
* wine (27)
* drunk (26)
* bottle (26)
* knives (19)
* pills (18)

### birds
* only 21!

In [3]:
Counter(reverseJackson).most_common(350)

[('the', 2516),
 ('and', 1684),
 ('i', 1452),
 ('a', 1204),
 ('in', 1131),
 ('to', 1083),
 ('my', 864),
 ('of', 856),
 ('you', 670),
 ('on', 430),
 ('like', 390),
 ('your', 356),
 ('is', 350),
 ('me', 339),
 ('with', 336),
 ('it', 314),
 ('that', 311),
 ('but', 303),
 ('we', 290),
 ('all', 274),
 ('for', 274),
 ("i'm", 268),
 ('when', 262),
 ('out', 254),
 ('or', 241),
 ('this', 229),
 ('at', 204),
 ('was', 202),
 ('her', 198),
 ('up', 191),
 ('our', 183),
 ('are', 171),
 ('into', 171),
 ('his', 171),
 ('as', 168),
 ('from', 158),
 ('no', 156),
 ('how', 153),
 ('have', 148),
 ('she', 147),
 ('so', 144),
 ("it's", 141),
 ('not', 140),
 ('know', 138),
 ("don't", 136),
 ('through', 135),
 ('be', 135),
 ('one', 131),
 ('about', 131),
 ('back', 129),
 ('their', 122),
 ('they', 122),
 ('them', 121),
 ('just', 118),
 ('if', 117),
 ('there', 110),
 ('will', 106),
 ('he', 106),
 ('an', 105),
 ('these', 103),
 ('where', 101),
 ('were', 100),
 ('over', 100),
 ('what', 99),
 ('down', 96),
 ('can',

## Markov Models

Now we make a model of the text at different scales by making a dictionary of different words/phrases and what words come after them. The scale corresponds to how many words are in the "key", from 1 (very short and unpredictable) to 4 (rigid but more coherent). I'll be using different models to try and skew towards more coherence, dropping down to the next level if there are no valid words, until it finds a valid option.

For example, in his line, "*saying, Hit me, don't hit me, please hit me, do it now.*" We can make two simple tables at scales of 1 and 2 respectively:

| word | word that comes after (pair)|
| ---- | -------------------- |
| saying | hit|
| Hit | me, me, me|
| me | don't, please, do|
| don't | hit |
| please | hit |
| do | it |
| it | now|
| now | (end)|


| phrase (3 words) | word that comes after | 
| ---------------- | --------------------- |
| saying, hit | me |
| hit me | don't, please, do|
| me don't | hit|
| don't hit | me |
| me please | hit|
| please hit | me|
| me do | it|
| do it | now |
| it now | (end) |


*Reminder, for the following models, the words are reversed, so it's actually making note of what words are likely to preceed rather than follow.*

**But now we do it for the whole body of text...**

Functions courtesy of Allison Parrish:

In [4]:
def add_to_model(model, n, seq):
    # make a copy of seq and append None to the end
    seq = list(seq[:]) + [None]
    for i in range(len(seq)-n):
        # tuple because we're using it as a dict key!
        gram = tuple(seq[i:i+n])
        next_item = seq[i+n]            
        if gram not in model:
            model[gram] = []
        model[gram].append(next_item)

def markov_model(n, seq):
    model = {}
    add_to_model(model, n, seq)
    return model

In [218]:
# Scale 1 (word pairs)

Jackov_1 = markov_model(1, reverseJackson)
print(Jackov_1)

{('ones',): ['new', 'the', 'loved', 'loved', 'the', 'only', 'wild', 'only', 'the', 'new', 'small', 'the', 'loved', 'loved', 'mad', 'the'], ('new',): ['built', 'couple', 'and', 'something', 'a', 'these', 'find', 'their', 'this', 'a', 'my', 'with', 'finding', 'someone', 'one', 'your', 'your', 'a', 'with', 'a', 'the', 'no', 'something', 'nothing', 'a', 'the', 'every', 'a', 'a', 'the', 'anything', 'in'], ('built',): ['and', 'canada', 'freeway', 'and', 'ants'], ('and',): ['knees', 'hands', 'shop', 'brother', 'shovels', 'brother', 'up', 'hotel', 'friend', 'say', 'chest', 'drunk', 'medication', 'sunset', 'words', 'on', 'facelifts', 'shoes', 'eyes', 'photos', 'focus', 'up', 'foolish', 'fence', 'do', 'moonshine', 'dash', 'limit', 'me', 'whiskey', 'crickets', 'songs', 'sobbing', 'hair', 'white', 'beds', 'running', 'laughing', 'it', 'coffee', 'earlobes', 'edges', 'letters', 'complaint', 'kitchen', 'smalls', 'kitchen', 'prescriptions', 'sewers', 'temples', 'cleavage', 'throat', 'know', 'needles', 

In [6]:
# Scale 2 (3 word phrases)
Jackov_2 = markov_model(2, reverseJackson)

In [7]:
# Scale 3 (4 word phrases)
Jackov_3 = markov_model(3, reverseJackson)

In [8]:
# Scale 4 (4 word phrases)
Jackov_4 = markov_model(4, reverseJackson)
print(Jackov_4)

{('ones', 'new', 'built', 'and'): ['knees'], ('new', 'built', 'and', 'knees'): ['and'], ('built', 'and', 'knees', 'and'): ['hands'], ('and', 'knees', 'and', 'hands'): ['our'], ('knees', 'and', 'hands', 'our'): ['on'], ('and', 'hands', 'our', 'on'): ['got'], ('hands', 'our', 'on', 'got'): ['we'], ('our', 'on', 'got', 'we'): ['so'], ('on', 'got', 'we', 'so'): ['castles'], ('got', 'we', 'so', 'castles'): ['the'], ('we', 'so', 'castles', 'the'): ['all'], ('so', 'castles', 'the', 'all'): ['destroyed'], ('castles', 'the', 'all', 'destroyed'): ['already'], ('the', 'all', 'destroyed', 'already'): ['had'], ('all', 'destroyed', 'already', 'had'): ['someone'], ('destroyed', 'already', 'had', 'someone'): ['smash'], ('already', 'had', 'someone', 'smash'): ['to'], ('had', 'someone', 'smash', 'to'): ['nothing'], ('someone', 'smash', 'to', 'nothing'): ['was'], ('smash', 'to', 'nothing', 'was'): ['there'], ('to', 'nothing', 'was', 'there'): ['boardwalk'], ('nothing', 'was', 'there', 'boardwalk'): ['the

## Rhyming

So now for the fun stuff. We can use the CMU Pronouncing Dictionary to process all of the phonemes in Jackson's poems and make a similar dictionary to the markov models, only these will categorize words by their end phonemes. 

To demonstrate, I'm going to use a different version of the original poem file to generate some rhyming couplets of his words. In fact, we can make rhyming sonnets of his existing lines right now and be done with it, but for my goal of correct Iambic pentameter, we have to go the long way 'round.

In [9]:
demoRhymes = defaultdict(list)
for line in open("../txt/JacksonCorpus_Apr19.txt"):
    line = line.strip("\n.,;:?!")
    words = line.split()
    if len(words)>0:
        last_word = words[-1]
        phones = pr.phones_for_word(last_word)
        if len(phones)>0:
            rhyming_part = pr.rhyming_part(phones[0])
            demoRhymes[rhyming_part].append(line)

In [10]:
demoRhymes

defaultdict(list,
            {'IY2': ['ELEGY',
              'APOSTROPHE',
              "My body's holding itself together like origami",
              'ones in the Little Company',
              'for you and that someone is probably',
              "but I've only ended up with an elegy",
              "I can't help but think of Katrina and that company",
              "watching a kid puke in an ambulance I'm probably",
              "we'll be dropping water balloons from atop the library",
              'in his backyard, kept company',
              'ELEGY',
              "for a drink or a smoke, and I'm feeling a bit like a honeybee"],
             'OW1 N': ["We were the ones slow-dancing with streetlamps, fashioning gallows out of bottle and bone, we were singing from the tops of pines, the birds didn't know what to make of us and our scramble towards the sky, we were building walls in the backyard and knocking them down the next morning, on the metro we were always swimming in po

In [13]:
rhyme = random.choice(list(demoRhymes.keys()))
random.sample(demoRhymes[rhyme], 2)

['from the east. Last night I chased Jaeger',
 'Tonight I want to take a knee to the blind beggar']

In [18]:
# this sonnet doesn't prevent words from having the same rhyming word
sonnet = []
for i in range(3):
    firstRhyme = random.choice(list(demoRhymes.keys()))
    while len(demoRhymes[firstRhyme]) <= 2:
        firstRhyme = random.choice(list(demoRhymes.keys()))
#         print('test')
    print(firstRhyme)
    secondRhyme = random.choice(list(demoRhymes.keys()))
    while len(demoRhymes[secondRhyme]) <= 2:
        secondRhyme = random.choice(list(demoRhymes.keys()))
    print(secondRhyme)
    firstCouplet = random.sample(demoRhymes[firstRhyme], 2)
    while firstCouplet[0].split()[-4:] == firstCouplet[1].split()[-4:]:
        firstCouplet = random.sample(demoRhymes[firstRhyme], 2)
        print(firstCouplet)
    secondCouplet = random.sample(demoRhymes[secondRhyme], 2)
    while secondCouplet[0].split()[-4:] == secondCouplet[1].split()[-4:]:
        secondCouplet = random.sample(demoRhymes[secondRhyme], 2)
        print(secondCouplet)
    sonnet.append(firstCouplet[0])
    sonnet.append(secondCouplet[0])
    sonnet.append(firstCouplet[1])
    sonnet.append(secondCouplet[1])
lastRhyme = random.choice(list(demoRhymes.keys()))
while len(demoRhymes[lastRhyme]) <= 2:
    lastRhyme = random.choice(list(demoRhymes.keys()))
    print(lastRhyme)
lastCouplet = random.sample(demoRhymes[lastRhyme], 2)
while lastCouplet[0].split()[-4:] == lastCouplet[1].split()[-4:]:
        lastCouplet = random.sample(demoRhymes[lastRhyme], 2)
sonnet.append(lastCouplet[0])
sonnet.append(lastCouplet[1])

IY1 CH
IH1 K S
EY1 K S
EH1 V ER0
UW1 S
IH1 R ER0 Z
EH1 K
EH2 T
AE1 F


In [19]:
sonnet

['in gloom, headlights reach',
 'flood my brain with tics',
 'plant them in the soil, and wait. Crows bathe in bleach',
 'a nervous habit of dragging them across chain links and bricks',
 'Maybe it takes and takes',
 "I lob into crowds, and I'm so damn clever",
 'Rinse, dry, repeat. Valium, lithium, booze, dandruff flakes',
 'yourself in light, how you could never',
 "let's put a little something in our orange juice",
 "won't explode. I've been boxing in halls of mirrors",
 "got tangled in the screen, I didn't pull it loose",
 'in the libraries and morgues, in the faint messages scrawled in mirrors',
 'one junkie says next door, and his friends laugh',
 "I'm not here to clip your wings, laugh"]

In [21]:
# this sonnet doesn't allow the same word ends, but it's harder to find ones that work
sonnet2 = []
for i in range(3):
    firstRhyme = random.choice(list(demoRhymes.keys()))
    while len(demoRhymes[firstRhyme]) <= 3:
        firstRhyme = random.choice(list(demoRhymes.keys()))
#         print('test')
    print(firstRhyme)
    secondRhyme = random.choice(list(demoRhymes.keys()))
    while len(demoRhymes[secondRhyme]) <= 3:
        secondRhyme = random.choice(list(demoRhymes.keys()))
    print(secondRhyme)
    firstCouplet = random.sample(demoRhymes[firstRhyme], 2)
    while firstCouplet[0].split()[-1] == firstCouplet[1].split()[-1]:
        firstCouplet = random.sample(demoRhymes[firstRhyme], 2)
#         print(firstCouplet)
    secondCouplet = random.sample(demoRhymes[secondRhyme], 2)
    while secondCouplet[0].split()[-1] == secondCouplet[1].split()[-1]:
        secondCouplet = random.sample(demoRhymes[secondRhyme], 2)
#         print(secondCouplet)
    sonnet2.append(firstCouplet[0])
    sonnet2.append(secondCouplet[0])
    sonnet2.append(firstCouplet[1])
    sonnet2.append(secondCouplet[1])
lastRhyme = random.choice(list(demoRhymes.keys()))
while len(demoRhymes[lastRhyme]) <= 3:
    lastRhyme = random.choice(list(demoRhymes.keys()))
    print(lastRhyme)
lastCouplet = random.sample(demoRhymes[lastRhyme], 2)
while lastCouplet[0].split()[-1] == lastCouplet[1].split()[-1]:
        lastCouplet = random.sample(demoRhymes[lastRhyme], 2)
sonnet2.append(lastCouplet[0])
sonnet2.append(lastCouplet[1])

IH1 R
EY1 B AH0 L
UW1 Z
UW1 V
OW1 IH0 NG
IH1 S T AH0 L
IY1 K


In [22]:
sonnet2

["My matchbook's instructions are clear",
 "have actually read a PBR can's label",
 'and people will notice the stench of fear',
 'on our imaginary coffee table',
 'shaky with the booze',
 'black widows whenever I find them. I hope she would approve',
 "It's embarrassing how often I lose",
 'from ravaging the dance floor. Nobody move',
 'again—too many smokes and nights not knowing',
 'FINGER PISTOL',
 "I don't believe in your love either. I'm going",
 'just pulled up in his jacked-up Ford—his sideburns and pistol',
 "just in case I want them back. I pull out my widow's peak",
 "it feels like God's just taking a leak"]

So now we're going to make a new dictionary of all the words and their phonemes, so instead of picking from pre-written lines, we're just picking the rhyming words and generating new lines in reverse from the rhyme word seeds.

In [23]:
rhymes = defaultdict(list)
for word in reverseJackson:
    if word not in rhymes.values():
        phones = pr.phones_for_word(word)
        if len(phones)>0:
            rhyming_part = pr.rhyming_part(phones[0])
            rhymes[rhyming_part].append(word)
# should remove duplicates, but w/e

In [24]:
rhymes

defaultdict(list,
            {'AH1 N Z': ['ones',
              'ones',
              'ones',
              'runs',
              'ones',
              "one's",
              'ones',
              'ones',
              'ones',
              "nun's",
              'runs',
              "one's",
              'ones',
              "sun's",
              'runs',
              "one's",
              'ones',
              'ones',
              'ones',
              'runs',
              "one's",
              'ones',
              'ones',
              'runs',
              'ones',
              'ones',
              'ones'],
             'UW1': ['new',
              'to',
              'to',
              'to',
              'to',
              'too',
              'too',
              'you',
              'to',
              'do',
              'you',
              'you',
              'you',
              'you',
              'you',
              'to',
              'you',
             

## Stresses

Now we can explore the Pronouncing stress search functions, by seeing if there are any prexisting lines in Jackson's poems that are already in iambic pentameter:

In [25]:
# redoing the corpus so the words are in the right order
newCorpus = open("JBotCorpus.txt").read().strip("\n.,;:?!").lower()
JackTxt = newCorpus.replace(",","").replace(".","").replace("—"," ").replace("?","")
JackTxt = JackTxt.split()

# now just scanning through the whole document to find
# any sequence of words that match iambic pentameter
ipLines = []
stressCheck = "0101010101"
newLine = ""
match = stressCheck
for word in JackTxt:
    phones = pr.phones_for_word(word)
    if len(phones)>0:
        wordStress = pr.stresses(phones[0])
#       because we don't care about the difference between 2 and 1
        wordStress = wordStress.replace("2", "1")
#         if wordStress == "01":
#             print(word)
        if match.find(wordStress) == 0:
            newLine += word + " "
            match = match[len(wordStress):]
            if len(match) == 0:
                ipLines.append(newLine)
                newLine = ""
                match = stressCheck
        else:
            newLine = ""
            match = stressCheck
            
print(ipLines)

['sedated than alive and living yes ', 'and smokes and weekly tutor sessions where ', 'and wilbur offer me a smoke and i ', 'the colored panels on the walls and then ', 'the bishop or the devil twiddling his ', 'in our pockets ghosts in our ears ', 'and tossed across a thousand yards and then ', 'a punching bag depending on the day ', 'the supermarkets all the houses all ', "another person's body like the teeth ", 'a couple lighters gain a couple friends ', 'and fly away remove the bullet from ', 'the show a mother was defending her ', 'abandon then nostalgia now the man ', "a walking pilot light and i'm the place ", 'a hive expecting honey you and i ', 'the cushions like a quarter or a lost ', 'the nozzles draped in yellow tape the green ', 'in sand and pulling free whenever you ', 'a woman screaming bible verses through ', 'because another stranger died the news ', 'the crashes or the falls the waiting rooms ', 'balloons behind a rusted waving to ', 'and pistol say hello hello hello 

In [26]:
ipRhymes = defaultdict(list)
for line in ipLines:
#     line = line.strip("\n.,;:?!")
    words = line.split()
    if len(words)>0:
        last_word = words[-1]
        phones = pr.phones_for_word(last_word)
        if len(phones)>0:
            rhyming_part = pr.rhyming_part(phones[0])
            ipRhymes[rhyming_part].append(line)
ipRhymes   

defaultdict(list,
            {'EH1 S': ['sedated than alive and living yes '],
             'EH1 R': ['and smokes and weekly tutor sessions where '],
             'AY1': ['and wilbur offer me a smoke and i ',
              'a hive expecting honey you and i ',
              'and morgues without a second thought and i '],
             'EH1 N': ['the colored panels on the walls and then ',
              'and tossed across a thousand yards and then '],
             'IH1 Z': ['the bishop or the devil twiddling his '],
             'IH1 R Z': ['in our pockets ghosts in our ears '],
             'EY1': ['a punching bag depending on the day ',
              'become accustomed to the disarray '],
             'AO1 L': ['the supermarkets all the houses all ',
              'a razor rather than a sheath and all '],
             'IY1 TH': ["another person's body like the teeth "],
             'EH1 N D Z': ['a couple lighters gain a couple friends '],
             'AH1 M': ['and fly away remove t

In [37]:
# newIP = {}
# for rhyme in ipRhymes:
#     if len(ipRhymes[rhyme])>=2:
#         newIP.update(rhyme)
        
ipSonnet = []
for i in range(3):
    firstRhyme = random.choice(list(ipRhymes.keys()))
    while len(ipRhymes[firstRhyme]) <= 1:
        firstRhyme = random.choice(list(ipRhymes.keys()))
#         print('test')
    print(firstRhyme)
    secondRhyme = random.choice(list(ipRhymes.keys()))
    while len(ipRhymes[secondRhyme]) <= 1:
        secondRhyme = random.choice(list(ipRhymes.keys()))
    print(secondRhyme)
    firstCouplet = random.sample(ipRhymes[firstRhyme], 2)
    while firstCouplet[0].split()[-4:] == firstCouplet[1].split()[-4:]:
        firstCouplet = random.sample(ipRhymes[firstRhyme], 2)
        print(firstCouplet)
    secondCouplet = random.sample(ipRhymes[secondRhyme], 2)
    while secondCouplet[0].split()[-4:] == secondCouplet[1].split()[-4:]:
        secondCouplet = random.sample(demoRhymes[secondRhyme], 2)
        print(secondCouplet)
    ipSonnet.append(firstCouplet[0])
    ipSonnet.append(secondCouplet[0])
    ipSonnet.append(firstCouplet[1])
    ipSonnet.append(secondCouplet[1])
lastRhyme = random.choice(list(ipRhymes.keys()))
while len(demoRhymes[lastRhyme]) <= 1:
    lastRhyme = random.choice(list(ipRhymes.keys()))
    print(lastRhyme)
lastCouplet = random.sample(ipRhymes[lastRhyme], 2)
while lastCouplet[0].split()[-4:] == lastCouplet[1].split()[-4:]:
        lastCouplet = random.sample(ipRhymes[lastRhyme], 2)
ipSonnet.append(lastCouplet[0])
ipSonnet.append(lastCouplet[1])

AO1 L
ER1
['Here in this droning 4am blur', 'black coffee is chain smoking in Big Sur']
UW1
EH1 N
AO1 L
UW1


In [38]:
ipSonnet

['the supermarkets all the houses all ',
 'Here in this droning 4am blur',
 'a razor rather than a sheath and all ',
 'black coffee is chain smoking in Big Sur',
 'in sand and pulling free whenever you ',
 'the colored panels on the walls and then ',
 'balloons behind a rusted waving to ',
 'and tossed across a thousand yards and then ',
 'a razor rather than a sheath and all ',
 'in sand and pulling free whenever you ',
 'the supermarkets all the houses all ',
 'balloons behind a rusted waving to ',
 'balloons behind a rusted waving to ',
 'in sand and pulling free whenever you ']

# SHOW TIME MON AMI

Here's where the magic happens

In [39]:
# need to start with rhyme seeds, 7 phoneme parts
# then follow same sonnet structure
# with each, need to generate lines starting with markov 4
# removing incorrect stressed words from the lists, moving down a level when out
# then once you have the full five feet, add it to the list

# to start, just generate one line in iambic pentameter

In [45]:
Jackov_1.keys()

dict_keys([('ones',), ('new',), ('built',), ('and',), ('knees',), ('hands',), ('our',), ('on',), ('got',), ('we',), ('so',), ('castles',), ('the',), ('all',), ('destroyed',), ('already',), ('had',), ('someone',), ('smash',), ('to',), ('nothing',), ('was',), ('there',), ('boardwalk',), ('shop',), ('taffy',), ('past',), ('out',), ('beach',), ('finally',), ('i',), ('brother',), ('my',), ('when',), ('something',), ('for',), ('looking',), ('flashlights',), ('shovels',), ('with',), ('eleven',), ('at',), ('went',), ('night',), ('last',), ('because',), ('ruined',), ("they're",), ('down',), ('up',), ('sand',), ('of',), ('dozens',), ('hotel',), ('rehoboth',), ('outside',), ('lines',), ('power',), ('in',), ('tangled',), ('kite',), ('a',), ("there's",), ('mouth',), ('blood',), ('is',), ('why',), ('some',), ('throats',), ('caught',), ('longer',), ('no',), ('are',), ('pills',), ('until',), ('laugh',), ('we’ll',), ('friend',), ('from',), ('stolen',), ('i’ve',), ('car',), ('adams',), ('drive',), ('i’l

In [46]:
Jackov_1[('dropping',)]

['dying', 'been', 'be', "i'm", 'of', 'are', 'faces']

In [238]:
#one couplet test
def get_seed():
    seed = random.choice(list(rhymes.keys()))
    while len(rhymes[seed]) <= 1:
        seed = random.choice(list(rhymes.keys()))
    seedPair = random.sample(rhymes[seed], 2)
    return seedPair

def get_pair():
    seedTest = get_seed()
    while seedTest[0] == seedTest[1]:
        seedTest = get_seed()
    return seedTest

def get_newStress():
    stressPair = get_pair()
    firstStress = pr.stresses(pr.phones_for_word(stressPair[0])[0]).replace("2", "1")
    secondStress = pr.stresses(pr.phones_for_word(stressPair[1])[0]).replace("2", "1")
    return [stressPair, firstStress, secondStress]

def get_stressedPair():
#     stressPair = get_pair()
#     firstStress = pr.stresses(pr.phones_for_word(stressPair[0])[0]).replace("2", "1")
#     secondStress = pr.stresses(pr.phones_for_word(stressPair[1])[0]).replace("2", "1")
    stressChunk = get_newStress()
    ipStress = "0101010101"    
#     while (firstStress != ipStress[-len(firstStress):]) or (secondStress != ipStress[-len(secondStress):]):
#         print(firstStress, len(firstStress), ipStress[-len(firstStress):])
    while (stressChunk[1] != ipStress[-len(stressChunk[1]):]) or (stressChunk[2] != ipStress[-len(stressChunk[2]):]):
#         print(stressChunk)
        stressChunk = get_newStress()
    return stressChunk

In [239]:
get_stressedPair()

[['lawns', "dawn's"], '1', '1']

In [240]:
nextWords1 = [word for word in Jackov_1[('follow',)]] #chunk [0][0]
stressCheck1 = "0101010101"
stressCheck1 = stressCheck1[:-len('01')] #chunk[1]
penta1 = ""
toe = random.choice(nextWords1)
while pr.stresses(pr.phones_for_word(toe)[0]).replace("2","1") != stressCheck1[:-len(toe)]:
    print(toe, pr.stresses(pr.phones_for_word(toe)[0]), stressCheck1[:-len(pr.stresses(pr.phones_for_word(toe)[0]))])
    nextWords1.remove(toe)
    if len(nextWords1) > 0:
        toe = random.choice(nextWords1)
    else:
         print("void")


to 1 0101010
i 1 0101010
we'll 1 0101010
to 1 0101010
them 1 0101010
they 1 0101010
untouched 01 010101
didn't 10 010101
to 1 0101010
to 1 0101010
void
to 1 0101010


ValueError: list.remove(x): x not in list

In [222]:
Jackov_1[('follow',)]

['they', "we'll", 'i', 'them', 'untouched', 'to', 'to', 'to', "didn't", 'to']

In [260]:
def find_next_word(nextWords, currentStress, pentaLine):
    #random.choice, if matches, continue, if not, new seed, if none left, return bad
    toe = random.choice(nextWords)
    while pr.stresses(pr.phones_for_word(toe)[0]).replace("2","1") != currentStress[:-len(toe)]:
        if len(nextWords) > 0:
            print(toe, pr.stresses(pr.phones_for_word(toe)[0]), currentStress[:-len(pr.stresses(pr.phones_for_word(toe)[0]))])
            nextWords.remove(toe)
            toe = random.choice(nextWords)
        else:
            print(toe, pr.stresses(pr.phones_for_word(toe)[0]), currentStress[:-len(pr.stresses(pr.phones_for_word(toe)[0]))])
            return "void"
    

def gen_penta(chunk):
    #make new str w seed word, new stress with end off
    nextWords1 = [word for word in Jackov_1[(chunk[0][0],)]]
    print(nextWords1)
    stressCheck1 = "0101010101"
    stressCheck1 = stressCheck1[:-len(chunk[1])] #chunk[1]
    penta1 = chunk[0][0]
    print(penta1)
    checkChunk = find_next_word(nextWords1, stressCheck1, penta1)
    if checkChunk == "void":
        return "void"
    print(len(checkChunk))
    else:
        while len(checkChunk) = 3:
            while checkChunk[1] != '':
                checkChunk = find_next_word(checkChunk[0], checkChunk[1], checkChunk[2])
        
    #if return bad, start over,
    #else if stress not done, find next
    # else if done, return line
    print(checkChunk)
    
# if line void, get another word from that list,
# if list runs out, go back one word
# if go back to first list and all words have been checked, get new seeds
#

SyntaxError: invalid syntax (<ipython-input-260-403b6f67f5a4>, line 26)

In [259]:
gen_penta(get_stressedPair())

['mr', 'mr']
colt
mr 10 0101010
mr 10 0101010


IndexError: Cannot choose from an empty sequence

In [342]:
chunk = get_stressedPair()
nextWords1 = [word for word in Jackov_1[(chunk[0][0],)]]
print(nextWords1)
stressCheck1 = "0101010101"
stressCheck1 = stressCheck1[:-len(chunk[1])] #chunk[1]
print(stressCheck1)
penta1 = [chunk[0][0]]
print(penta1)
# checkChunk = find_next_word(nextWords1, stressCheck1, penta1)
foot = random.choice(nextWords1)
nextWords1.remove(foot)
footPhones = pr.phones_for_word(foot)
print("FOOT FPEONE", footPhones)
if len(footPhones)>0:
    footStress = pr.stresses(footPhones[0])
else:
    print("error", foot, footPhones)
print(foot, footStress, stressCheck1[-len(footStress):])

while len(stressCheck1) > 0:
    if footStress == stressCheck1[-len(footStress):]:
        print("good")
        nextWords1 = [word for word in Jackov_1[(foot,)]]
        stressCheck1 = stressCheck1[:-len(footStress)]
        penta1.insert(0, foot)
        print ("new word", stressCheck1, penta1)
        foot = random.choice(nextWords1)
        nextWords1.remove(foot)
        footPhones = pr.phones_for_word(foot)
        if len(footPhones)>0:
            footStress = pr.stresses(footPhones[0])
        else:
            print("error", foot, footPhones)
        print("FOOT FPEONE", footPhones)
#         footStress = pr.stresses(pr.phones_for_word(foot)[0])
        print(foot, footStress, stressCheck1[-len(footStress):])
    elif len(nextWords1) > 0:
        foot = random.choice(nextWords1)
        nextWords1.remove(foot)
        footPhones = pr.phones_for_word(foot)
        if len(footPhones)>0:
            footStress = pr.stresses(footPhones[0])
        else:
            print("error", foot, footPhones)
        print("FOOT FPEONE", footPhones)
#         footStress = pr.stresses(footPhones[0])
#         footStress = pr.stresses(pr.phones_for_word(foot)[0])
        print(foot, footStress, stressCheck1[-len(footStress):])
        print("next")
#         break
    else:
        print("void")
        break
        
# penta1.insert(0, foot)
print("FINISHED LINE:", " ".join(penta1))
    


['a', 'by', 'fridge', 'the', 'of', 'horny', 'enough', 'the', 'and', 'dragging', 'seeing']
010101010
['stray']
FOOT FPEONE ['IH0 N AH1 F', 'IY0 N AH1 F']
enough 01 10
FOOT FPEONE ['DH AH0', 'DH AH1', 'DH IY0']
the 0 0
next
good
new word 01010101 ['the', 'stray']
FOOT FPEONE ['AH0 N D', 'AE1 N D']
and 0 1
FOOT FPEONE ['L UH1 K S']
looks 1 1
next
good
new word 0101010 ['looks', 'the', 'stray']
FOOT FPEONE ['HH IY1']
he 1 0
FOOT FPEONE ['F EY1 S']
face 1 0
next
FOOT FPEONE ['EH1 V R IY0 TH IH2 NG']
everything 102 010
next
FOOT FPEONE ['L AH1 V ER0']
lover 10 10
next
good
new word 01010 ['lover', 'looks', 'the', 'stray']
FOOT FPEONE ['M AY1']
my 1 0
FOOT FPEONE ['Y AO1 R', 'Y UH1 R']
your 1 0
next
FOOT FPEONE ['Y AO1 R', 'Y UH1 R']
your 1 0
next
FOOT FPEONE ['M AY1']
my 1 0
next
FOOT FPEONE ['Y AO1 R', 'Y UH1 R']
your 1 0
next
FOOT FPEONE ['IH2 M AE1 JH AH0 N EH2 R IY0']
imaginary 21020 01010
next
FOOT FPEONE ['M AY1']
my 1 0
next
FOOT FPEONE ['AH0', 'EY1']
a 0 0
next
good
new word 0101 ['a

In [400]:
#okay lets do this
finalLines = []
def get_pentaCouplet():
    chunk = get_stressedPair()
    nextWords1 = [word for word in Jackov_1[(chunk[0][0],)]]
#     print(nextWords1)
    stressCheck1 = "0101010101"
    stressCheck1 = stressCheck1[:-len(chunk[1])] #chunk[1]
#     print(stressCheck1)
    penta1 = [chunk[0][0]]
#     print(penta1)
    # checkChunk = find_next_word(nextWords1, stressCheck1, penta1)
    foot = random.choice(nextWords1)
    nextWords1.remove(foot)
    footPhones = pr.phones_for_word(foot)
#     print("FOOT FPEONE", footPhones)
    if len(footPhones)>0:
        footStress = pr.stresses(footPhones[0])
    else:
        get_pentaCouplet()
        return
#         print("error", foot, footPhones)
#     print(foot, footStress, stressCheck1[-len(footStress):])

    while len(stressCheck1) > 0:
        if footStress == stressCheck1[-len(footStress):]:
#             print("good")
            nextWords1 = [word for word in Jackov_1[(foot,)]]
            stressCheck1 = stressCheck1[:-len(footStress)]
            penta1.insert(0, foot)
#             print ("new word", stressCheck1, penta1)
            foot = random.choice(nextWords1)
            nextWords1.remove(foot)
            footPhones = pr.phones_for_word(foot)
            if len(footPhones)>0:
                footStress = pr.stresses(footPhones[0])
            else:
#                 print("error", foot, footPhones)
                get_pentaCouplet()
                return
#             print("FOOT FPEONE", footPhones)
#             print(foot, footStress, stressCheck1[-len(footStress):])
        elif len(nextWords1) > 0:
            foot = random.choice(nextWords1)
            nextWords1.remove(foot)
            footPhones = pr.phones_for_word(foot)
            if len(footPhones)>0:
                footStress = pr.stresses(footPhones[0])
            else:
#                 print("error", foot, footPhones)
                get_pentaCouplet()
                return
#             print("FOOT FPEONE", footPhones)
#             print(foot, footStress, stressCheck1[-len(footStress):])
#             print("next")
    #         break
        else:
#             print("void")
            get_pentaCouplet()
            return

#     penta1.insert(0, foot)
    print("FINISHED LINE 1:", " ".join(penta1))
    
    nextWords2 = [word for word in Jackov_1[(chunk[0][1],)]]
#     print(nextWords2)
    stressCheck2 = "0101010101"
    stressCheck2 = stressCheck2[:-len(chunk[2])] #chunk[1]
#     print(stressCheck2)
    penta2 = [chunk[0][1]]
#     print(penta2)
    foot = random.choice(nextWords2)
    nextWords2.remove(foot)
    footPhones = pr.phones_for_word(foot)
#     print("FOOT FPEONE", footPhones)
    if len(footPhones)>0:
        footStress = pr.stresses(footPhones[0])
    else:
        get_pentaCouplet()
        return
#         print("error", foot, footPhones)
#     print(foot, footStress, stressCheck2[-len(footStress):])

    while len(stressCheck2) > 0:
        if footStress == stressCheck2[-len(footStress):]:
#             print("good")
            nextWords2 = [word for word in Jackov_1[(foot,)]]
            stressCheck2 = stressCheck2[:-len(footStress)]
            penta2.insert(0, foot)
#             print ("new word", stressCheck2, penta2)
            foot = random.choice(nextWords2)
            nextWords2.remove(foot)
            footPhones = pr.phones_for_word(foot)
            if len(footPhones)>0:
                footStress = pr.stresses(footPhones[0])
            else:
#                 print("error", foot, footPhones)
                get_pentaCouplet()
#                 break
                return
#             print("FOOT FPEONE", footPhones)
#             print(foot, footStress, stressCheck2[-len(footStress):])
        elif len(nextWords2) > 0:
            foot = random.choice(nextWords2)
            nextWords2.remove(foot)
            footPhones = pr.phones_for_word(foot)
            if len(footPhones)>0:
                footStress = pr.stresses(footPhones[0])
            else:
#                 print("error", foot, footPhones)
                get_pentaCouplet()
                return
#             print("FOOT FPEONE", footPhones)
#             print(foot, footStress, stressCheck2[-len(footStress):])
#             print("next")
    #         break
        else:
#             print("void")
            get_pentaCouplet()
            return

#     penta2.insert(0, foot)
    print("FINISHED LINE 2:", " ".join(penta2))
    
    print("COUPLET")
    print("")
    print("")
    print("")
    print(" ".join(penta1))
    print(" ".join(penta2))
    
    coupA = " ".join(penta1)
    coupB = " ".join(penta2)
    
    finalLines.append([coupA, coupB])
    return([coupA, coupB])
    
    
    


In [376]:
get_pentaCouplet()

['i', 'i', 'i']
010101010
['dreamed']
FOOT FPEONE ['AY1']
i 1 0
FOOT FPEONE ['AY1']
i 1 0
next
FOOT FPEONE ['AY1']
i 1 0
next
void
['to', 'we']
01010101
['reflect']
FOOT FPEONE ['T UW1', 'T IH0', 'T AH0']
to 1 1
good
new word 0101010 ['to', 'reflect']
FOOT FPEONE ['W AA1 N T S', 'W AO1 N T S']
wants 1 0
FOOT FPEONE ['K ER1 S IH0 Z']
curses 10 10
next
good
new word 01010 ['curses', 'to', 'reflect']
FOOT FPEONE ['M AH1 M B AH0 L IH0 NG', 'M AH1 M B L IH0 NG']
mumbling 100 010
FOOT FPEONE ['HH OW1 L IY0']
holy 10 10
next
good
new word 010 ['holy', 'curses', 'to', 'reflect']
FOOT FPEONE ['S EY1 M']
same 1 0
FOOT FPEONE ['Y UW1']
you 1 0
next
FOOT FPEONE ['DH OW1 Z']
those 1 0
next
FOOT FPEONE ['S IH1 N S']
since 1 0
next
FOOT FPEONE ['N AA1 T']
not 1 0
next
FOOT FPEONE ['S IH1 N S']
since 1 0
next
FOOT FPEONE ['L AY1 K']
like 1 0
next
FOOT FPEONE ['Y UW1']
you 1 0
next
FOOT FPEONE ['DH AH0', 'DH AH1', 'DH IY0']
the 0 0
next
good
new word 01 ['the', 'holy', 'curses', 'to', 'reflect']
FOOT F

'restarting'

In [377]:
get_pentaCouplet()

['their', 'calling']
010101010
['cabs']
FOOT FPEONE ['K AO1 L IH0 NG']
calling 10 10
good
new word 0101010 ['calling', 'cabs']
FOOT FPEONE ['AH0 N D', 'AE1 N D']
and 0 0
good
new word 010101 ['and', 'calling', 'cabs']
FOOT FPEONE ['G AE1 S P IH0 NG']
gasping 10 01
FOOT FPEONE ['M EH1 N']
men 1 1
next
good
new word 01010 ['men', 'and', 'calling', 'cabs']
FOOT FPEONE ['AE1 NG G R IY0']
angry 10 10
good
new word 010 ['angry', 'men', 'and', 'calling', 'cabs']
FOOT FPEONE ['W EY1']
way 1 0
FOOT FPEONE ['AE1 N', 'AH0 N']
an 1 0
next
FOOT FPEONE ['IH0 N', 'IH1 N']
in 0 0
next
good
new word 01 ['in', 'angry', 'men', 'and', 'calling', 'cabs']
FOOT FPEONE ['CH AY1 L D']
child 1 1
good
new word 0 ['child', 'in', 'angry', 'men', 'and', 'calling', 'cabs']
FOOT FPEONE ['HH ER1', 'HH ER0']
her 1 0
FOOT FPEONE ['HH ER1', 'HH ER0']
her 1 0
next
FOOT FPEONE ['DH EH1 R']
their 1 0
next
FOOT FPEONE ['HH ER1', 'HH ER0']
her 1 0
next
FOOT FPEONE ['HH ER1', 'HH ER0']
her 1 0
next
void
['do', 'on', 'hand', 'f

'restarting'

In [412]:
finalLines = []
aLines = get_pentaCouplet()
bLines = get_pentaCouplet()
cLines = get_pentaCouplet()
dLines = get_pentaCouplet()
eLines = get_pentaCouplet()
fLines = get_pentaCouplet()
gLines = get_pentaCouplet()

# print(finalLines)
finalSonnet = []
finalSonnet.append(finalLines[0][0])
finalSonnet.append(finalLines[1][0])
finalSonnet.append(finalLines[0][1])
finalSonnet.append(finalLines[1][1])
finalSonnet.append(finalLines[2][0])
finalSonnet.append(finalLines[3][0])
finalSonnet.append(finalLines[2][1])
finalSonnet.append(finalLines[3][1])
finalSonnet.append(finalLines[4][0])
finalSonnet.append(finalLines[5][0])
finalSonnet.append(finalLines[4][1])
finalSonnet.append(finalLines[5][1])
finalSonnet.append(finalLines[6][0])
finalSonnet.append(finalLines[6][1])

# for i in range(len(finalSonnet)-1):
#     print(finalSonnet[i])

print(finalSonnet)
print("")
print("")
print("")
print("")
print("")

for line in finalSonnet:
    print(line)

FINISHED LINE 1: in our window chewing or the bridge
FINISHED LINE 1: and our cabin like a bottle some
FINISHED LINE 1: a burning with the only one receive
FINISHED LINE 1: the nothing only have a couple graves
FINISHED LINE 1: a toaster something from atop the end
FINISHED LINE 1: the devil's beating sinus morphine while
FINISHED LINE 1: already naked bodies clad in strange
FINISHED LINE 2: and lucky pen in bright and takes a change
COUPLET



already naked bodies clad in strange
and lucky pen in bright and takes a change
FINISHED LINE 1: receipts the altar made and her the land
FINISHED LINE 2: and take a night and wouldn't understand
COUPLET



receipts the altar made and her the land
and take a night and wouldn't understand
FINISHED LINE 1: in our shoes and warm and nails the porch
FINISHED LINE 1: the couch and doing something never had
FINISHED LINE 1: enamored watching me the frigid bronze
FINISHED LINE 1: in any semblance of the many times
FINISHED LINE 1: a city making faces c